In [1]:
import torch
from copy import copy
from tqdm import tqdm

from experiments.experiment import Experiment
from experiments.parser import get_parser
from rvae.misc import brownian_motion_sample
from rvae.vizualization.visualization_new import (
    create_metric_heatmap,
    overlay_kde_contours,
)

parser = get_parser()
args = parser.parse_args(
    args=[
        "--model",
        "RVAE",
        "--dataset",
        "fmnist",
        "--enc_layers",
        "300",
        "300",
        "--dec_layers",
        "300",
        "300",
        "--latent_dim",
        "2",
        "--num_centers",
        "350",
        "--num_components",
        "1",
        "--device",
        "cpu",
        "--ckpt_path",
        "/home/prz/PROJECTS/rvae_reproduction/saved_models/RVAE/fmnist_epoch100ckpt",
    ]
)
exp = Experiment(args)
exp.load_just_model(pretrained_path=args.ckpt_path)
exp.model._mean_warmup = False
device = torch.device("cuda") if torch.cuda.is_available() else torch.device("cpu")

DEBUG: self.rvae_save_dir='../saved_models/RVAE/' | os.path.exists(self.rvae_save_dir)=True


/home/prz/PROJECTS/rvae_reproduction/rvae/utils/save_utils.py:28: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  checkpoint = torch.load(load_path, map_location="cpu")


---

In [2]:
# NOTE: consider conditional vae and notice howform the brownian motion changes

In [3]:
heatmap_fig = create_metric_heatmap(model=exp.model, side=110, step=1, device=device)

In [4]:
from rvae.vizualization.visualization_new import extract_latent_samples
from rvae.vizualization.visualization_new import overlay_bm_samples_gradient

In [5]:
samples, labels, idxs = extract_latent_samples(
    model=exp.model, data_loader=exp.train_loader
)

Embedding datapoints: 600it [00:08, 72.06it/s]


In [17]:
oheatmap_fig = overlay_kde_contours(
    heatmap_fig=copy(heatmap_fig), data_tensor=samples, line_width=1, show_points=False
)

In [16]:
init_points = [
    [0, 0],
    [-17, 5],
    [-10, -13],
    [-40, 50],
    [16, 27],
    [23, -1],
    [19, 3],
    [-3, 13],
]
bm_samples = []

for init_point in tqdm(init_points):
    bm_samples.append(
        brownian_motion_sample(
            num_steps=1000,
            num_samples=1,
            dim=2,
            t=200,
            init_point=torch.tensor(init_point, dtype=torch.float32),
            model=exp.model,
        )
    )

100%|██████████| 8/8 [01:05<00:00,  8.24s/it]


In [18]:
for init_point, bm_sample in tqdm(zip(init_points, bm_samples)):
    oheatmap_fig = overlay_bm_samples_gradient(
        heatmap_fig=oheatmap_fig,
        bm_samples=bm_sample,
        line_width=2,
        marker_size=3,
        name_sufix=f" {tuple(init_point)}",
    )

8it [00:11,  1.47s/it]


In [20]:
oheatmap_fig.write_html("brownian_motion-0.html")

In [19]:
oheatmap_fig